In [1]:
from echo_map import *

import hvplot.xarray


In [2]:
from pathlib import Path

import numpy as np
import xarray as xr

import echopype as ep

base_dpath = Path('./exports')
base_dpath.mkdir(exist_ok=True)

converted_dpath = Path(base_dpath / 'hakesurvey_convertednc')
converted_dpath.mkdir(exist_ok=True)
calibrated_dpath = (base_dpath / 'hakesurvey_calibratednc')
calibrated_dpath.mkdir(exist_ok=True)

for datapath in converted_dpath.glob('*'):
    ed = ep.open_converted(datapath)
    
platform_ds = xr.open_mfdataset(
    str(converted_dpath / '*.zarr'), group='Platform', 
    engine='zarr',
    data_vars='minimal', coords='minimal',
    combine='nested'
)

MVBS_test = xr.open_mfdataset(
    str(calibrated_dpath / 'MVBS_*.nc'), 
    data_vars='minimal', coords='minimal',
    combine='by_coords'
)

lon = platform_ds["longitude"][
                platform_ds["sentence_type"] == "GGA"]


lat = platform_ds["latitude"][
                platform_ds["sentence_type"] == "GGA"]

lon=lon.interp(time1=MVBS_test["ping_time"])
lat=lat.interp(time1=MVBS_test["ping_time"])

MVBS_test["longitude"]=lon
MVBS_test["latitude"]=lat

import datetime
history = (
        f"{datetime.datetime.utcnow()} +00:00. "
        "Interpolated from Platform latitude/longitude."
    )

MVBS_test["latitude"] = MVBS_test["latitude"].assign_attrs({"history": history})
MVBS_test["longitude"] = MVBS_test["longitude"].assign_attrs({"history": history})

MVBS_test

<xarray.Dataset>
Dimensions:            (ping_time: 515, channel: 3, echo_range: 150)
Coordinates:
  * ping_time          (ping_time) datetime64[ns] 2017-07-28T00:05:20 ... 201...
  * channel            (channel) object 'GPT  18 kHz 009072058c8d 1-1 ES18-11...
  * echo_range         (echo_range) float64 0.0 5.0 10.0 ... 735.0 740.0 745.0
    time1              (ping_time) datetime64[ns] 2017-07-28T00:05:20 ... 201...
Data variables:
    Sv                 (channel, ping_time, echo_range) float64 dask.array<chunksize=(3, 60, 150), meta=np.ndarray>
    frequency_nominal  (channel) float64 dask.array<chunksize=(3,), meta=np.ndarray>
    longitude          (ping_time) float64 dask.array<chunksize=(515,), meta=np.ndarray>
    latitude           (ping_time) float64 dask.array<chunksize=(515,), meta=np.ndarray>
Attributes:
    processing_software_name:     echopype
    processing_software_version:  0.6.0
    processing_time:              2022-07-07T18:29:33Z
    processing_function:          preprocess.compute_MVBS

In [4]:
import hvplot.xarray

gram=MVBS_test.Sv.sel(channel='GPT  18 kHz 009072058c8d 1-1 ES18-11').hvplot(
    kind='image',
    x='ping_time',
    y='echo_range',
    c='Sv', 
    title='Echogram',
    cmap='jet',
    flip_yaxis=True)
gram

:Image   [ping_time,echo_range]   (Sv)

In [ ]:
# def plot_track(platform_ds):
#     xr_dataset = geoviews.Dataset(platform_ds,
#                                   kdims=['time1'],
#                                   vdims=['longitude', 'latitude'])

#     ship_track = xr_dataset.to(geoviews.Path,
#                                kdims=['longitude', 'latitude'],
#                                vdims=['time1']).opts(width=600,
#                                                      height=450,
#                                                      color='blue',
#                                                      tools=['hover'])

#     return ship_track


# def plot_selected(bounds):
#     lon = MVBS_ds.sel(ping_time=slice(bounds[0], bounds[2])).longitude.values

#     lat = MVBS_ds.sel(ping_time=slice(bounds[0], bounds[2])).latitude.values

#     track = dict(Longitude=lon, Latitude=lat)

#     path = geoviews.Path([track]).opts(line_width=4, color='red', alpha=0.5)

#     begin = (lon[0], lat[0], 'begin')

#     end = (lon[-1], lat[-1], 'end')

#     points = geoviews.Points([begin, end]).opts(width=500,
#                                                 height=475,
#                                                 size=5,
#                                                 color='white')

#     return path * points


# def plot_bounds(box):

#     bounds = holoviews.DynamicMap(lambda bounds: holoviews.Bounds(bounds).opts(
#         line_width=1, line_color='white'),
#                                   streams=[box])

#     return bounds


# def plot_map(gram, MVBS_ds, map_tiles=geoviews.tile_sources.Wikipedia):

#     box = streams.BoundsXY(
#         source=gram,
#         bounds=(MVBS_ds.ping_time.values[0], MVBS_ds.echo_range.values[-1],
#                 MVBS_ds.ping_time.values[-1], MVBS_ds.echo_range.values[0]))

#     bounds = plot_bounds(box)

#     def plot_selected(bounds):
#         lon = MVBS_ds.sel(
#             ping_time=slice(bounds[0], bounds[2])).longitude.values

#         lat = MVBS_ds.sel(
#             ping_time=slice(bounds[0], bounds[2])).latitude.values

#         track = dict(Longitude=lon, Latitude=lat)

#         path = geoviews.Path([track]).opts(line_width=4,
#                                            color='red',
#                                            alpha=0.7)

#         begin = (lon[0], lat[0], 'begin')

#         end = (lon[-1], lat[-1], 'end')

#         points = geoviews.Points([begin, end]).opts(width=500,
#                                                     height=475,
#                                                     size=5,
#                                                     color='white')

#         return path * points * map_tiles

#     selected_are = holoviews.DynamicMap(plot_selected, streams=[box])

#     return gram * bounds + selected_are

In [5]:
x=plot_map(gram,MVBS_test)
x[0] + x[1]*plot_track(platform_ds)

:Layout
   .DynamicMap.I  :DynamicMap   []
      :Overlay
         .Image.I  :Image   [ping_time,echo_range]   (Sv)
         .Bounds.I :Bounds   [x,y]
   .DynamicMap.II :DynamicMap   []
      :Overlay
         .Path.I   :Path   [Longitude,Latitude]
         .Points.I :Points   [Longitude,Latitude]
         .WMTS.I   :WMTS   [Longitude,Latitude]
         .Path.II  :Path   [longitude,latitude]   (time1)